In [103]:
!git clone https://github.com/ultralytics/yolov5

Cloning into 'yolov5'...


In [104]:
cd yolov5

c:\Users\jedrz\Desktop\test_test\yolov5


In [105]:
pip install -r requirements.txt

  Using cached setuptools-67.8.0-py3-none-any.whl (1.1 MB)
Note: you may need to restart the kernel to use updated packages.


In [106]:
# Function to get the data from XML Annotation
def extract_info_from_xml(xml_file):
    root = ET.parse(xml_file).getroot()
    
    # Initialise the info dict 
    info_dict = {}
    info_dict['bboxes'] = []

    # Parse the XML Tree
    for elem in root:
        # Get the file name 
        if elem.tag == "filename":
            info_dict['filename'] = elem.text
            
        # Get the image size
        elif elem.tag == "size":
            image_size = []
            for subelem in elem:
                image_size.append(int(subelem.text))
            
            info_dict['image_size'] = tuple(image_size)
        
        # Get details of the bounding box 
        elif elem.tag == "object":
            bbox = {}
            for subelem in elem:
                if subelem.tag == "name":
                    bbox["class"] = subelem.text
                    
                elif subelem.tag == "bndbox":
                    for subsubelem in subelem:
                        bbox[subsubelem.tag] = int(float(subsubelem.text))         
            info_dict['bboxes'].append(bbox)
    
    return info_dict

In [108]:
print(extract_info_from_xml(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations\2007_000027.xml'))

{'bboxes': [{'class': 'person', 'xmin': 174, 'ymin': 101, 'xmax': 349, 'ymax': 351}], 'filename': '2007_000027.jpg', 'image_size': (486, 500, 3)}


In [109]:
# Dictionary that maps class names to IDs
class_name_to_id_mapping = {"person": 0,
                           "bird": 1,
                           "cat": 2,
                           "cow": 3,
                           "dog": 4,
                           "horse": 5,
                           "sheep": 6, 
                           "aeroplane": 7, 
                           "bicycle": 8,
                           "boat": 9,
                           "bus": 10,
                           "car": 11,
                           "motorbike": 12,
                           "train": 13,
                           "bottle": 14,
                           "chair": 15,
                           "diningtable": 16,
                           "pottedplant": 17,
                           "sofa": 18,
                           "tvmonitor": 19}

# Convert the info dict to the required yolo format and write it to disk
def convert_to_yolov5(info_dict):
    print_buffer = []
    
    # For each bounding box
    for b in info_dict["bboxes"]:
        try:
            class_id = class_name_to_id_mapping[b["class"]]
        except KeyError:
            print(class_id)
            print("Invalid Class. Must be one from ", class_name_to_id_mapping.keys())
            
        
        # Transform the bbox co-ordinates as per the format required by YOLO v5
        b_center_x = (b["xmin"] + b["xmax"]) / 2 
        b_center_y = (b["ymin"] + b["ymax"]) / 2
        b_width    = (b["xmax"] - b["xmin"])
        b_height   = (b["ymax"] - b["ymin"])
        
        # Normalise the co-ordinates by the dimensions of the image
        image_w, image_h, image_c = info_dict["image_size"]  
        b_center_x /= image_w 
        b_center_y /= image_h 
        b_width    /= image_w 
        b_height   /= image_h 
        
        #Write the bbox details to the file 
        print_buffer.append("{} {:.3f} {:.3f} {:.3f} {:.3f}".format(class_id, b_center_x, b_center_y, b_width, b_height))
        
    # Name of the file which we have to save 
    save_file_name = os.path.join(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations', info_dict["filename"].replace("jpg", "txt"))
    
    # Save the annotation to disk
    print("\n".join(print_buffer), file= open(save_file_name, "w"))

In [110]:
# Get the annotations
annotations = [os.path.join(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations', x) for x in os.listdir(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations') if x[-3:] == "xml"]
annotations.sort()

# Convert and save the annotations
for ann in tqdm(annotations):
    info_dict = extract_info_from_xml(ann)
    convert_to_yolov5(info_dict)

annotations = [os.path.join(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations', x) for x in os.listdir(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations') if x[-3:] == "txt"]


100%|███████████████████████████████████████████████████████████████████████████| 17125/17125 [01:52<00:00, 151.60it/s]


In [111]:
# Read images and annotations
images = [os.path.join(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\JPEGImages', x) for x in os.listdir(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\JPEGImages')]
annotations = [os.path.join(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations', x) for x in os.listdir(r'C:\Users\jedrz\Desktop\TEST_TEST\VOCdevkit\VOC2012\Annotations') if x[-3:] == "txt"]

images.sort()
annotations.sort()

# Split the dataset into train-valid-test splits 
train_images, val_images, train_annotations, val_annotations = train_test_split(images, annotations, test_size = 0.2, random_state = 1)
val_images, test_images, val_annotations, test_annotations = train_test_split(val_images, val_annotations, test_size = 0.5, random_state = 1)

ValueError: Found input variables with inconsistent numbers of samples: [0, 17125]

In [1]:
import torch

torch.zeros(1).cuda()


tensor([0.], device='cuda:0')

In [1]:
cd yolov5/


c:\Users\jedrz\Desktop\test_test\yolov5


In [3]:
!python train.py --img 640 --batch 16 --epochs 1 --data ./data/VisDrone.yaml --weights '' --cfg yolov5s.yaml --device 0


train: weights='', cfg=yolov5s.yaml, data=./data/VisDrone.yaml, hyp=data\hyps\hyp.scratch-low.yaml, epochs=1, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=None, image_weights=False, device=0, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github:  YOLOv5 is out of date by 2 commits. Use 'git pull' or 'git clone https://github.com/ultralytics/yolov5' to update.
YOLOv5  v7.0-183-g878d9c8 Python-3.11.4 torch-2.0.1+cu118 CUDA:0 (NVIDIA GeForce GTX 1050 Ti, 4096MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0

In [5]:
!python val.py --img 640 --data ./data/VisDrone.yaml --weights ./runs/train/exp16/weights/best.pt 

val: data=./data/VisDrone.yaml, weights=['./runs/train/exp16/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=val, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs\val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5  v7.0-183-g878d9c8 Python-3.11.4 torch-2.0.1+cu118 CUDA:0 (NVIDIA GeForce GTX 1050 Ti, 4096MiB)

Fusing layers... 
Model summary: 224 layers, 7080880 parameters, 0 gradients
Traceback (most recent call last):
  File "c:\Users\jedrz\Desktop\test_test\yolov5\val.py", line 409, in <module>
    main(opt)
  File "c:\Users\jedrz\Desktop\test_test\yolov5\val.py", line 380, in main
    run(**vars(opt))
  File "C:\Users\jedrz\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\torch\utils\_contextlib.py", line 115, in decorate_context
    return func(*args, *

In [3]:
!python val.py --img 640 --data ./data/coco.yaml --weights ./yolov5s.pt

loading annotations into memory...
Done (t=0.89s)
creating index...
index created!
Loading and preparing results...
DONE (t=10.34s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=48.38s).
Accumulating evaluation results...
DONE (t=21.77s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.001
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.002
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.001
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.002
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.001
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= large | maxDets=100 ] = 0.002
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets=  1 ] = 0.032
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets= 10 ] = 0.058
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxD

val: data=./data/coco.yaml, weights=['./yolov5s.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=val, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=True, project=runs\val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5  v7.0-183-g878d9c8 Python-3.11.4 torch-2.0.1+cu118 CUDA:0 (NVIDIA GeForce GTX 1050 Ti, 4096MiB)

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients

val: Scanning C:\Users\jedrz\Desktop\test_test\datasets\coco\labels\val2017...:   0%|          | 0/5000 [00:00<?, ?it/s]
val: Scanning C:\Users\jedrz\Desktop\test_test\datasets\coco\labels\val2017... 1 images, 0 backgrounds, 0 corrupt:   0%|          | 1/5000 [00:23<32:02:56, 23.08s/it]
val: Scanning C:\Users\jedrz\Desktop\test_test\datasets\coco\labels\val2017... 32 images, 0 backgrounds, 0 corrupt:   1%|          | 32/5000 [00:23<42:29,  1.95it/s] 
val: Scanning C:\Users\

In [3]:
!python train.py --img 640 --batch 14 --epochs 3 --data ./data/my_custom.yaml --weights '' --cfg yolov5s.yaml --device 0

train: weights='', cfg=yolov5s.yaml, data=./data/my_custom.yaml, hyp=data\hyps\hyp.scratch-low.yaml, epochs=3, batch_size=14, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=None, image_weights=False, device=0, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=6, project=runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github:  YOLOv5 is out of date by 2 commits. Use 'git pull' or 'git clone https://github.com/ultralytics/yolov5' to update.
YOLOv5  v7.0-183-g878d9c8 Python-3.11.4 torch-2.0.1+cu118 CUDA:0 (NVIDIA GeForce GTX 1050 Ti, 4096MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.

In [2]:
import torch
torch.cuda.empty_cache()

In [1]:
cd yolov5/

c:\Users\jedrz\Desktop\test_test\yolov5


In [9]:
!set 'PYTORCH_CUDA_ALLOC_CONF=max_split_size_mb:512'